In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
from copy import deepcopy
import logging

In [3]:
from torch.nn.parallel import DistributedDataParallel as DDP, DataParallel as DP

In [4]:
from torch_ecg_bak.torch_ecg.models._nets import BCEWithLogitsWithClassWeightLoss
from torch_ecg_bak.torch_ecg.utils.utils_nn import default_collate_fn as collate_fn
from torch_ecg_bak.torch_ecg.utils.misc import (
    init_logger, get_date_str, dict_to_str, str2bool,
)
from model import ECG_CRNN_CINC2021
from utils.scoring_metrics import evaluate_scores
from cfg import BaseCfg, TrainCfg, ModelCfg
from dataset import CINC2021

In [5]:
from train import train

In [6]:
TrainCfg.db_dir = "/home/wenh06/Jupyter/data/CinC2021/"

In [7]:
config = deepcopy(TrainCfg)
config.db_dir = "/home/wenh06/Jupyter/data/CinC2021/"

In [8]:
config

{'db_dir': '/home/wenh06/Jupyter/data/CinC2021/',
 'log_dir': '/home/wenh06/Jupyter/wenhao/workspace/cinc2021/log',
 'model_dir': '/home/wenh06/Jupyter/wenhao/workspace/cinc2021/saved_models',
 'final_model_name': None,
 'checkpoints': '/home/wenh06/Jupyter/wenhao/workspace/cinc2021/checkpoints',
 'keep_checkpoint_max': 20,
 'leads': ['I',
  'II',
  'III',
  'aVR',
  'aVL',
  'aVF',
  'V1',
  'V2',
  'V3',
  'V4',
  'V5',
  'V6'],
 'fs': 500,
 'data_format': 'channel_first',
 'special_classes': ['Brady', 'LAD', 'RAD', 'PR', 'LQRSV'],
 'normalize_data': True,
 'train_ratio': 0.8,
 'min_class_weight': 0.5,
 'tranches_for_training': '',
 'tranche_class_weights': {'A': {'AF': 0.7604422604422605,
   'IAVB': 1.2860110803324099,
   'CLBBB': 3.9343220338983054,
   'NSR': 1.011437908496732,
   'PAC': 1.5073051948051948,
   'CRBBB': 0.5},
  'B': {'AF': 0.9901960784313726,
   'AFL': 2.805555555555556,
   'CRBBB': 1.3289473684210529,
   'IAVB': 1.429245283018868,
   'IRBBB': 1.7616279069767442,
  

In [9]:
len(config.classes)

21

In [10]:
from cfg import six_leads, four_leads, three_leads, two_leads

In [11]:
ModelFilename = {
    n: f"{n}_lead_model_updated.pth.tar" for n in [12, 6, 4, 3, 2,]
}

### train 12-lead model

In [12]:
model_config = deepcopy(ModelCfg.twelve_leads)

In [13]:
model_config

{'cnn': {'name': 'multi_scopic_leadwise',
  'vgg16': {'num_convs': [2, 2, 3, 3, 3],
   'num_filters': [48, 96, 192, 384, 384],
   'groups': 1,
   'kernel_initializer': 'he_normal',
   'kw_initializer': {},
   'activation': 'relu',
   'kw_activation': {},
   'block': {'filter_length': 3,
    'subsample_length': 1,
    'dilation': 1,
    'batch_norm': True,
    'pool_size': 3,
    'pool_stride': 2,
    'kernel_initializer': 'he_normal',
    'kw_initializer': {},
    'activation': 'relu',
    'kw_activation': {}}},
  'vgg16_mish': {'num_convs': [2, 2, 3, 3, 3],
   'num_filters': [48, 96, 192, 384, 384],
   'groups': 1,
   'kernel_initializer': 'he_normal',
   'kw_initializer': {},
   'activation': 'relu',
   'kw_activation': {},
   'block': {'filter_length': 3,
    'subsample_length': 1,
    'dilation': 1,
    'batch_norm': True,
    'pool_size': 3,
    'pool_stride': 2,
    'kernel_initializer': 'he_normal',
    'kw_initializer': {},
    'activation': 'mish',
    'kw_activation': {}}},
 

In [14]:
model_config.cnn.name = config.cnn_name
model_config.rnn.name = config.rnn_name
model_config.attn.name = config.attn_name

In [15]:
config.n_leads = 12

config.final_model_name = ModelFilename[12]

In [16]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
logger = init_logger(log_dir=config.log_dir, verbose=2)
logger.info(f"\n{'*'*20}   Start Training   {'*'*20}\n")
logger.info(f"Using device {device}")
logger.info(f"Using torch of version {torch.__version__}")
logger.info(f"with configuration\n{dict_to_str(config)}")

tranches = config.tranches_for_training
if tranches:
    classes = config.tranche_classes[tranches]
else:
    classes = config.classes

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

log file path: /home/wenh06/Jupyter/wenhao/workspace/cinc2021/log/log_07-13_20-46.txt
levels of c_handler and f_handler are set DEBUG
ECG - INFO - 
********************   Start Training   ********************

ECG - INFO - Using device cuda


<IPython.core.display.Javascript object>

ECG - INFO - Using torch of version 1.8.1+cu111
ECG - INFO - with configuration
{
    "db_dir": "/home/wenh06/Jupyter/data/CinC2021/",
    "log_dir": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/log",
    "model_dir": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/saved_models",
    "final_model_name": "12_lead_model_updated.pth.tar",
    "checkpoints": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/checkpoints",
    "keep_checkpoint_max": 20,
    "leads": [
        "I",
        "II",
        "III",
        "aVR",
        "aVL",
        "aVF",
        "V1",
        "V2",
        "V3",
        "V4",
        "V5",
        "V6"
    ],
    "fs": 500,
    "data_format": "channel_first",
    "special_classes": [
        "Brady",
        "LAD",
        "RAD",
        "PR",
        "LQRSV"
    ],
    "normalize_data": True,
    "train_ratio": 0.8,
    "min_class_weight": 0.5,
    "tranches_for_training": "",
    "tranche_class_weights": {
        "A": {
            "AF": 0.760442260442260

In [17]:
model = ECG_CRNN_CINC2021(
    classes=classes,
    n_leads=config.n_leads,
    config=model_config,
)
model.__DEBUG__ = False

if torch.cuda.device_count() > 1:
    model = DP(model)
    # model = DDP(model)
model.to(device=device)

classes (totally 21) for prediction:['AF', 'AFL', 'BBB', 'CLBBB', 'CRBBB', 'IAVB', 'IRBBB', 'LAnFB', 'LPR', 'LQT', 'NSIVCB', 'NSR', 'PAC', 'PRWP', 'PVC', 'QAb', 'SA', 'SB', 'STach', 'TAb', 'TInv']
configuration of ECG_CRNN_CINC2021 is as follows
{
    "cnn": {
        "name": "multi_scopic_leadwise",
        "vgg16": {
            "num_convs": [
                2, 2, 3, 3, 3
            ],
            "num_filters": [
                48, 96, 192, 384, 384
            ],
            "groups": 1,
            "kernel_initializer": "he_normal",
            "kw_initializer": {},
            "activation": "relu",
            "kw_activation": {},
            "block": {
                "filter_length": 3,
                "subsample_length": 1,
                "dilation": 1,
                "batch_norm": True,
                "pool_size": 3,
                "pool_stride": 2,
                "kernel_initializer": "he_normal",
                "kw_initializer": {},
                "activation": "r

<IPython.core.display.Javascript object>

DataParallel(
  (module): ECG_CRNN_CINC2021(
    (cnn): MultiScopicCNN(
      (branches): ModuleDict(
        (branch_0): MultiScopicBranch(
          (block_0): MultiScopicBasicBlock(
            (ca_0): Conv_Bn_Activation(
              (conv1d): Conv1d(12, 192, kernel_size=(11,), stride=(1,), padding=(5,), groups=12)
              (batch_norm): GroupNorm(12, 192, eps=1e-05, affine=True)
              (activation_relu): ReLU(inplace=True)
            )
            (bn): BatchNorm1d(192, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
            (down): DownSample(
              (down_sample): MaxPool1d(kernel_size=2, stride=2, padding=0, dilation=1, ceil_mode=False)
            )
          )
          (block_1): MultiScopicBasicBlock(
            (ca_0): Conv_Bn_Activation(
              (conv1d): Conv1d(192, 384, kernel_size=(7,), stride=(1,), padding=(3,), groups=12)
              (batch_norm): GroupNorm(12, 384, eps=1e-05, affine=True)
              (activation_re

In [18]:
config.batch_size, config.n_epochs

(64, 40)

In [19]:
config.batch_size = 128

In [20]:
final_model = train(
    model=model,
    model_config=model_config,
    config=config,
    device=device,
    logger=logger,
    debug=True,
)

ECG - INFO - training configurations are as follows:
{
    "db_dir": "/home/wenh06/Jupyter/data/CinC2021/",
    "log_dir": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/log",
    "model_dir": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/saved_models",
    "final_model_name": "12_lead_model_updated.pth.tar",
    "checkpoints": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/checkpoints",
    "keep_checkpoint_max": 20,
    "leads": [
        "I",
        "II",
        "III",
        "aVR",
        "aVL",
        "aVF",
        "V1",
        "V2",
        "V3",
        "V4",
        "V5",
        "V6"
    ],
    "fs": 500,
    "data_format": "channel_first",
    "special_classes": [
        "Brady",
        "LAD",
        "RAD",
        "PR",
        "LQRSV"
    ],
    "normalize_data": True,
    "train_ratio": 0.8,
    "min_class_weight": 0.5,
    "tranches_for_training": "",
    "tranche_class_weights": {
        "A": {
            "AF": 0.7604422604422605,
            "IAVB": 1.28

log file path is set /home/wenh06/Jupyter/wenhao/workspace/cinc2021/working_dir/CinC2021-CinC2021.log
levels of c_handler and f_handler are set DEBUG

start performing train test split...

train test split finished in 0.02 minutes
log file path is set /home/wenh06/Jupyter/wenhao/workspace/cinc2021/working_dir/CinC2021-CinC2021.log
levels of c_handler and f_handler are set DEBUG

start performing train test split...

train test split finished in 0.02 minutes
log file path is set /home/wenh06/Jupyter/wenhao/workspace/cinc2021/working_dir/CinC2021-CinC2021.log
levels of c_handler and f_handler are set DEBUG

start performing train test split...

train test split finished in 0.02 minutes
ECG - INFO - 
Starting training:
------------------
Epochs:          40
Batch size:      128
Learning rate:   0.001
Training size:   61944
Validation size: 15505
Device:          cuda
Optimizer:       adamw_amsgrad
Dataset classes: ['AF', 'AFL', 'BBB', 'CLBBB', 'CRBBB', 'IAVB', 'IRBBB', 'LAnFB', 'LPR', 'LQ

Epoch 1/40:   4%|█                          | 2432/61944 [00:43<13:22, 74.15it/s, loss (batch)=1.43]

ECG - INFO - Train step_20: loss : 1.4281067848205566


Epoch 1/40:   8%|██                        | 4992/61944 [01:16<13:56, 68.12it/s, loss (batch)=0.883]

...

INFO:ECG:
Train epoch_27:
--------------------
train/epoch_loss:        198.09410655498505
train/auroc:             0.9917317560696769
train/auprc:             0.9340428749097572
train/accuracy:          0.7422994963192561
train/f_measure:         0.8526059491926897
train/f_beta_measure:    0.820353694629769
train/g_beta_measure:    0.6595242169135327
train/challenge_metric:  0.7613491113185274

test/auroc:              0.0
test/auprc:              nan
test/accuracy:           0.6315382134795228
test/f_measure:          0.5787628339635388
test/f_beta_measure:     0.5430291503324389
test/g_beta_measure:     0.3587942777125336
test/challenge_metric:   0.6214542692779171
---------------------------------



ECG - INFO - early stopping is triggered at epoch 27


INFO:ECG:early stopping is triggered at epoch 27
Epoch 27/40: 100%|███████████████████████| 61944/61944 [09:54<00:00, 104.15it/s, loss (batch)=0.461]

ECG - INFO - Best model saved to /home/wenh06/Jupyter/wenhao/workspace/cinc2021/saved_models/12_lead_model_updated.pth.tar!



INFO:ECG:Best model saved to /home/wenh06/Jupyter/wenhao/workspace/cinc2021/saved_models/12_lead_model_updated.pth.tar!


In [ ]:
logging.shutdown()

In [21]:
with torch.no_grad():
    torch.cuda.empty_cache()

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

### train 6-lead model

In [22]:
config.leads = six_leads
config.n_leads = 6
config.final_model_name = ModelFilename[6]

config.batch_size = 128

model_config = deepcopy(ModelCfg.six_leads)
model_config.cnn.name = config.cnn_name
model_config.rnn.name = config.rnn_name
model_config.attn.name = config.attn_name

In [23]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

del logger

logger = init_logger(log_dir=config.log_dir, verbose=2)
logger.info(f"\n{'*'*20}   Start Training   {'*'*20}\n")
logger.info(f"Using device {device}")
logger.info(f"Using torch of version {torch.__version__}")
logger.info(f"with configuration\n{dict_to_str(config)}")

tranches = config.tranches_for_training
if tranches:
    classes = config.tranche_classes[tranches]
else:
    classes = config.classes

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

log file path: /home/wenh06/Jupyter/wenhao/workspace/cinc2021/log/log_07-14_01-37.txt
levels of c_handler and f_handler are set DEBUG
ECG - INFO - 
********************   Start Training   ********************

ECG - INFO - 
********************   Start Training   ********************



INFO:ECG:
********************   Start Training   ********************



ECG - INFO - Using device cuda
ECG - INFO - Using device cuda


...

ECG - INFO - Using torch of version 1.8.1+cu111
ECG - INFO - Using torch of version 1.8.1+cu111


INFO:ECG:Using torch of version 1.8.1+cu111


ECG - INFO - with configuration
{
    "db_dir": "/home/wenh06/Jupyter/data/CinC2021/",
    "log_dir": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/log",
    "model_dir": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/saved_models",
    "final_model_name": "6_lead_model_updated.pth.tar",
    "checkpoints": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/checkpoints",
    "keep_checkpoint_max": 20,
    "leads": [
        "I",
        "II",
        "III",
        "aVR",
        "aVL",
        "aVF"
    ],
    "fs": 500,
    "data_format": "channel_first",
    "special_classes": [
        "Brady",
        "LAD",
        "RAD",
        "PR",
        "LQRSV"
    ],
    "normalize_data": True,
    "train_ratio": 0.8,
    "min_class_weight": 0.5,
    "tranches_for_training": "",
    "tranche_class_weights": {
        "A": {
            "AF": 0.7604422604422605,
            "IAVB": 1.2860110803324099,
            "CLBBB": 3.9343220338983054,
            "NSR": 1.011437908496732,
           

ECG - INFO - with configuration
{
    "db_dir": "/home/wenh06/Jupyter/data/CinC2021/",
    "log_dir": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/log",
    "model_dir": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/saved_models",
    "final_model_name": "6_lead_model_updated.pth.tar",
    "checkpoints": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/checkpoints",
    "keep_checkpoint_max": 20,
    "leads": [
        "I",
        "II",
        "III",
        "aVR",
        "aVL",
        "aVF"
    ],
    "fs": 500,
    "data_format": "channel_first",
    "special_classes": [
        "Brady",
        "LAD",
        "RAD",
        "PR",
        "LQRSV"
    ],
    "normalize_data": True,
    "train_ratio": 0.8,
    "min_class_weight": 0.5,
    "tranches_for_training": "",
    "tranche_class_weights": {
        "A": {
            "AF": 0.7604422604422605,
            "IAVB": 1.2860110803324099,
            "CLBBB": 3.9343220338983054,
            "NSR": 1.011437908496732,
           

INFO:ECG:with configuration
{
    "db_dir": "/home/wenh06/Jupyter/data/CinC2021/",
    "log_dir": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/log",
    "model_dir": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/saved_models",
    "final_model_name": "6_lead_model_updated.pth.tar",
    "checkpoints": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/checkpoints",
    "keep_checkpoint_max": 20,
    "leads": [
        "I",
        "II",
        "III",
        "aVR",
        "aVL",
        "aVF"
    ],
    "fs": 500,
    "data_format": "channel_first",
    "special_classes": [
        "Brady",
        "LAD",
        "RAD",
        "PR",
        "LQRSV"
    ],
    "normalize_data": True,
    "train_ratio": 0.8,
    "min_class_weight": 0.5,
    "tranches_for_training": "",
    "tranche_class_weights": {
        "A": {
            "AF": 0.7604422604422605,
            "IAVB": 1.2860110803324099,
            "CLBBB": 3.9343220338983054,
            "NSR": 1.011437908496732,
            "PA

In [24]:
model = ECG_CRNN_CINC2021(
    classes=classes,
    n_leads=config.n_leads,
    config=model_config,
)
model.__DEBUG__ = False

if torch.cuda.device_count() > 1:
    model = DP(model)
    # model = DDP(model)
model.to(device=device)

classes (totally 21) for prediction:['AF', 'AFL', 'BBB', 'CLBBB', 'CRBBB', 'IAVB', 'IRBBB', 'LAnFB', 'LPR', 'LQT', 'NSIVCB', 'NSR', 'PAC', 'PRWP', 'PVC', 'QAb', 'SA', 'SB', 'STach', 'TAb', 'TInv']
configuration of ECG_CRNN_CINC2021 is as follows
{
    "cnn": {
        "name": "multi_scopic_leadwise",
        "vgg16": {
            "num_convs": [
                2, 2, 3, 3, 3
            ],
            "num_filters": [
                48, 96, 192, 384, 384
            ],
            "groups": 1,
            "kernel_initializer": "he_normal",
            "kw_initializer": {},
            "activation": "relu",
            "kw_activation": {},
            "block": {
                "filter_length": 3,
                "subsample_length": 1,
                "dilation": 1,
                "batch_norm": True,
                "pool_size": 3,
                "pool_stride": 2,
                "kernel_initializer": "he_normal",
                "kw_initializer": {},
                "activation": "r

<IPython.core.display.Javascript object>

DataParallel(
  (module): ECG_CRNN_CINC2021(
    (cnn): MultiScopicCNN(
      (branches): ModuleDict(
        (branch_0): MultiScopicBranch(
          (block_0): MultiScopicBasicBlock(
            (ca_0): Conv_Bn_Activation(
              (conv1d): Conv1d(6, 144, kernel_size=(11,), stride=(1,), padding=(5,), groups=6)
              (batch_norm): GroupNorm(6, 144, eps=1e-05, affine=True)
              (activation_relu): ReLU(inplace=True)
            )
            (bn): BatchNorm1d(144, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
            (down): DownSample(
              (down_sample): MaxPool1d(kernel_size=2, stride=2, padding=0, dilation=1, ceil_mode=False)
            )
          )
          (block_1): MultiScopicBasicBlock(
            (ca_0): Conv_Bn_Activation(
              (conv1d): Conv1d(144, 288, kernel_size=(7,), stride=(1,), padding=(3,), groups=6)
              (batch_norm): GroupNorm(6, 288, eps=1e-05, affine=True)
              (activation_relu): 

In [25]:
final_model = train(
    model=model,
    model_config=model_config,
    config=config,
    device=device,
    logger=logger,
    debug=True,
)

ECG - INFO - training configurations are as follows:
{
    "db_dir": "/home/wenh06/Jupyter/data/CinC2021/",
    "log_dir": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/log",
    "model_dir": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/saved_models",
    "final_model_name": "6_lead_model_updated.pth.tar",
    "checkpoints": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/checkpoints",
    "keep_checkpoint_max": 20,
    "leads": [
        "I",
        "II",
        "III",
        "aVR",
        "aVL",
        "aVF"
    ],
    "fs": 500,
    "data_format": "channel_first",
    "special_classes": [
        "Brady",
        "LAD",
        "RAD",
        "PR",
        "LQRSV"
    ],
    "normalize_data": True,
    "train_ratio": 0.8,
    "min_class_weight": 0.5,
    "tranches_for_training": "",
    "tranche_class_weights": {
        "A": {
            "AF": 0.7604422604422605,
            "IAVB": 1.2860110803324099,
            "CLBBB": 3.9343220338983054,
            "NSR": 1.0114379

ECG - INFO - training configurations are as follows:
{
    "db_dir": "/home/wenh06/Jupyter/data/CinC2021/",
    "log_dir": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/log",
    "model_dir": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/saved_models",
    "final_model_name": "6_lead_model_updated.pth.tar",
    "checkpoints": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/checkpoints",
    "keep_checkpoint_max": 20,
    "leads": [
        "I",
        "II",
        "III",
        "aVR",
        "aVL",
        "aVF"
    ],
    "fs": 500,
    "data_format": "channel_first",
    "special_classes": [
        "Brady",
        "LAD",
        "RAD",
        "PR",
        "LQRSV"
    ],
    "normalize_data": True,
    "train_ratio": 0.8,
    "min_class_weight": 0.5,
    "tranches_for_training": "",
    "tranche_class_weights": {
        "A": {
            "AF": 0.7604422604422605,
            "IAVB": 1.2860110803324099,
            "CLBBB": 3.9343220338983054,
            "NSR": 1.0114379

INFO:ECG:training configurations are as follows:
{
    "db_dir": "/home/wenh06/Jupyter/data/CinC2021/",
    "log_dir": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/log",
    "model_dir": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/saved_models",
    "final_model_name": "6_lead_model_updated.pth.tar",
    "checkpoints": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/checkpoints",
    "keep_checkpoint_max": 20,
    "leads": [
        "I",
        "II",
        "III",
        "aVR",
        "aVL",
        "aVF"
    ],
    "fs": 500,
    "data_format": "channel_first",
    "special_classes": [
        "Brady",
        "LAD",
        "RAD",
        "PR",
        "LQRSV"
    ],
    "normalize_data": True,
    "train_ratio": 0.8,
    "min_class_weight": 0.5,
    "tranches_for_training": "",
    "tranche_class_weights": {
        "A": {
            "AF": 0.7604422604422605,
            "IAVB": 1.2860110803324099,
            "CLBBB": 3.9343220338983054,
            "NSR": 1.01143790849

log file path is set /home/wenh06/Jupyter/wenhao/workspace/cinc2021/working_dir/CinC2021-CinC2021.log
levels of c_handler and f_handler are set DEBUG

start performing train test split...

train test split finished in 0.02 minutes
log file path is set /home/wenh06/Jupyter/wenhao/workspace/cinc2021/working_dir/CinC2021-CinC2021.log
levels of c_handler and f_handler are set DEBUG

start performing train test split...

train test split finished in 0.02 minutes
log file path is set /home/wenh06/Jupyter/wenhao/workspace/cinc2021/working_dir/CinC2021-CinC2021.log
levels of c_handler and f_handler are set DEBUG

start performing train test split...

train test split finished in 0.02 minutes
ECG - INFO - 
Starting training:
------------------
Epochs:          40
Batch size:      128
Learning rate:   0.001
Training size:   61944
Validation size: 15505
Device:          cuda
Optimizer:       adamw_amsgrad
Dataset classes: ['AF', 'AFL', 'BBB', 'CLBBB', 'CRBBB', 'IAVB', 'IRBBB', 'LAnFB', 'LPR', 'LQ

INFO:ECG:
Starting training:
------------------
Epochs:          40
Batch size:      128
Learning rate:   0.001
Training size:   61944
Validation size: 15505
Device:          cuda
Optimizer:       adamw_amsgrad
Dataset classes: ['AF', 'AFL', 'BBB', 'CLBBB', 'CRBBB', 'IAVB', 'IRBBB', 'LAnFB', 'LPR', 'LQT', 'NSIVCB', 'NSR', 'PAC', 'PRWP', 'PVC', 'QAb', 'SA', 'SB', 'STach', 'TAb', 'TInv']
Class weights:   tensor([[ 2.7578,  1.7252, 28.8333,  9.6690,  2.9920,  4.0876,  7.7789,  6.6082,
 36.8508,  7.5750,  8.1752,  0.5000,  4.4339, 22.6418,  7.4538,  6.9583,
  3.8135,  0.7636,  1.4977,  1.2330,  3.6222]])
-----------------------------------------

Epoch 1/40:   4%|█                         | 2432/61944 [00:09<02:37, 377.14it/s, loss (batch)=1.01]

...

INFO:ECG:
Train epoch_31:
--------------------
train/epoch_loss:        199.64253574609756
train/auroc:             0.9891468282056008
train/auprc:             0.9229611450380223
train/accuracy:          0.7222329846312798
train/f_measure:         0.8247241734343466
train/f_beta_measure:    0.7795548311398744
train/g_beta_measure:    0.605716697232575
train/challenge_metric:  0.7375182756467134

test/auroc:              0.8737260401490721
test/auprc:              0.5540776847940135
test/accuracy:           0.6105127378265076
test/f_measure:          0.5129624754137772
test/f_beta_measure:     0.4790323051083491
test/g_beta_measure:     0.32150335054320295
test/challenge_metric:   0.5892663838716772
---------------------------------



ECG - INFO - early stopping is triggered at epoch 31
ECG - INFO - early stopping is triggered at epoch 31


INFO:ECG:early stopping is triggered at epoch 31
Epoch 31/40: 100%|███████████████████████| 61944/61944 [08:48<00:00, 117.28it/s, loss (batch)=0.458]

ECG - INFO - Best model saved to /home/wenh06/Jupyter/wenhao/workspace/cinc2021/saved_models/6_lead_model_updated.pth.tar!
ECG - INFO - Best model saved to /home/wenh06/Jupyter/wenhao/workspace/cinc2021/saved_models/6_lead_model_updated.pth.tar!



INFO:ECG:Best model saved to /home/wenh06/Jupyter/wenhao/workspace/cinc2021/saved_models/6_lead_model_updated.pth.tar!


In [ ]:
logging.shutdown()

In [26]:
with torch.no_grad():
    torch.cuda.empty_cache()

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

### train 4-lead model

In [27]:
config.leads = four_leads
config.n_leads = 4
config.final_model_name = ModelFilename[4]

config.batch_size = 256

model_config = deepcopy(ModelCfg.four_leads)
model_config.cnn.name = config.cnn_name
model_config.rnn.name = config.rnn_name
model_config.attn.name = config.attn_name

In [28]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

del logger

logger = init_logger(log_dir=config.log_dir, verbose=2)
logger.info(f"\n{'*'*20}   Start Training   {'*'*20}\n")
logger.info(f"Using device {device}")
logger.info(f"Using torch of version {torch.__version__}")
logger.info(f"with configuration\n{dict_to_str(config)}")

tranches = config.tranches_for_training
if tranches:
    classes = config.tranche_classes[tranches]
else:
    classes = config.classes

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

log file path: /home/wenh06/Jupyter/wenhao/workspace/cinc2021/log/log_07-14_06-05.txt
levels of c_handler and f_handler are set DEBUG
ECG - INFO - 
********************   Start Training   ********************

ECG - INFO - 
********************   Start Training   ********************

ECG - INFO - 
********************   Start Training   ********************



INFO:ECG:
********************   Start Training   ********************



ECG - INFO - Using device cuda
ECG - INFO - Using device cuda
ECG - INFO - Using device cuda


...

INFO:ECG:Using torch of version 1.8.1+cu111


ECG - INFO - with configuration
{
    "db_dir": "/home/wenh06/Jupyter/data/CinC2021/",
    "log_dir": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/log",
    "model_dir": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/saved_models",
    "final_model_name": "4_lead_model_updated.pth.tar",
    "checkpoints": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/checkpoints",
    "keep_checkpoint_max": 20,
    "leads": [
        "I",
        "II",
        "III",
        "V2"
    ],
    "fs": 500,
    "data_format": "channel_first",
    "special_classes": [
        "Brady",
        "LAD",
        "RAD",
        "PR",
        "LQRSV"
    ],
    "normalize_data": True,
    "train_ratio": 0.8,
    "min_class_weight": 0.5,
    "tranches_for_training": "",
    "tranche_class_weights": {
        "A": {
            "AF": 0.7604422604422605,
            "IAVB": 1.2860110803324099,
            "CLBBB": 3.9343220338983054,
            "NSR": 1.011437908496732,
            "PAC": 1.5073051948051948,
   

ECG - INFO - with configuration
{
    "db_dir": "/home/wenh06/Jupyter/data/CinC2021/",
    "log_dir": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/log",
    "model_dir": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/saved_models",
    "final_model_name": "4_lead_model_updated.pth.tar",
    "checkpoints": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/checkpoints",
    "keep_checkpoint_max": 20,
    "leads": [
        "I",
        "II",
        "III",
        "V2"
    ],
    "fs": 500,
    "data_format": "channel_first",
    "special_classes": [
        "Brady",
        "LAD",
        "RAD",
        "PR",
        "LQRSV"
    ],
    "normalize_data": True,
    "train_ratio": 0.8,
    "min_class_weight": 0.5,
    "tranches_for_training": "",
    "tranche_class_weights": {
        "A": {
            "AF": 0.7604422604422605,
            "IAVB": 1.2860110803324099,
            "CLBBB": 3.9343220338983054,
            "NSR": 1.011437908496732,
            "PAC": 1.5073051948051948,
   

ECG - INFO - with configuration
{
    "db_dir": "/home/wenh06/Jupyter/data/CinC2021/",
    "log_dir": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/log",
    "model_dir": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/saved_models",
    "final_model_name": "4_lead_model_updated.pth.tar",
    "checkpoints": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/checkpoints",
    "keep_checkpoint_max": 20,
    "leads": [
        "I",
        "II",
        "III",
        "V2"
    ],
    "fs": 500,
    "data_format": "channel_first",
    "special_classes": [
        "Brady",
        "LAD",
        "RAD",
        "PR",
        "LQRSV"
    ],
    "normalize_data": True,
    "train_ratio": 0.8,
    "min_class_weight": 0.5,
    "tranches_for_training": "",
    "tranche_class_weights": {
        "A": {
            "AF": 0.7604422604422605,
            "IAVB": 1.2860110803324099,
            "CLBBB": 3.9343220338983054,
            "NSR": 1.011437908496732,
            "PAC": 1.5073051948051948,
   

INFO:ECG:with configuration
{
    "db_dir": "/home/wenh06/Jupyter/data/CinC2021/",
    "log_dir": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/log",
    "model_dir": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/saved_models",
    "final_model_name": "4_lead_model_updated.pth.tar",
    "checkpoints": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/checkpoints",
    "keep_checkpoint_max": 20,
    "leads": [
        "I",
        "II",
        "III",
        "V2"
    ],
    "fs": 500,
    "data_format": "channel_first",
    "special_classes": [
        "Brady",
        "LAD",
        "RAD",
        "PR",
        "LQRSV"
    ],
    "normalize_data": True,
    "train_ratio": 0.8,
    "min_class_weight": 0.5,
    "tranches_for_training": "",
    "tranche_class_weights": {
        "A": {
            "AF": 0.7604422604422605,
            "IAVB": 1.2860110803324099,
            "CLBBB": 3.9343220338983054,
            "NSR": 1.011437908496732,
            "PAC": 1.5073051948051948,
       

In [29]:
model = ECG_CRNN_CINC2021(
    classes=classes,
    n_leads=config.n_leads,
    config=model_config,
)
model.__DEBUG__ = False

if torch.cuda.device_count() > 1:
    model = DP(model)
    # model = DDP(model)
model.to(device=device)

classes (totally 21) for prediction:['AF', 'AFL', 'BBB', 'CLBBB', 'CRBBB', 'IAVB', 'IRBBB', 'LAnFB', 'LPR', 'LQT', 'NSIVCB', 'NSR', 'PAC', 'PRWP', 'PVC', 'QAb', 'SA', 'SB', 'STach', 'TAb', 'TInv']
configuration of ECG_CRNN_CINC2021 is as follows
{
    "cnn": {
        "name": "multi_scopic_leadwise",
        "vgg16": {
            "num_convs": [
                2, 2, 3, 3, 3
            ],
            "num_filters": [
                48, 96, 192, 384, 384
            ],
            "groups": 1,
            "kernel_initializer": "he_normal",
            "kw_initializer": {},
            "activation": "relu",
            "kw_activation": {},
            "block": {
                "filter_length": 3,
                "subsample_length": 1,
                "dilation": 1,
                "batch_norm": True,
                "pool_size": 3,
                "pool_stride": 2,
                "kernel_initializer": "he_normal",
                "kw_initializer": {},
                "activation": "r

<IPython.core.display.Javascript object>

DataParallel(
  (module): ECG_CRNN_CINC2021(
    (cnn): MultiScopicCNN(
      (branches): ModuleDict(
        (branch_0): MultiScopicBranch(
          (block_0): MultiScopicBasicBlock(
            (ca_0): Conv_Bn_Activation(
              (conv1d): Conv1d(4, 96, kernel_size=(11,), stride=(1,), padding=(5,), groups=4)
              (batch_norm): GroupNorm(4, 96, eps=1e-05, affine=True)
              (activation_relu): ReLU(inplace=True)
            )
            (bn): BatchNorm1d(96, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
            (down): DownSample(
              (down_sample): MaxPool1d(kernel_size=2, stride=2, padding=0, dilation=1, ceil_mode=False)
            )
          )
          (block_1): MultiScopicBasicBlock(
            (ca_0): Conv_Bn_Activation(
              (conv1d): Conv1d(96, 192, kernel_size=(7,), stride=(1,), padding=(3,), groups=4)
              (batch_norm): GroupNorm(4, 192, eps=1e-05, affine=True)
              (activation_relu): ReLU

In [30]:
final_model = train(
    model=model,
    model_config=model_config,
    config=config,
    device=device,
    logger=logger,
    debug=True,
)

ECG - INFO - training configurations are as follows:
{
    "db_dir": "/home/wenh06/Jupyter/data/CinC2021/",
    "log_dir": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/log",
    "model_dir": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/saved_models",
    "final_model_name": "4_lead_model_updated.pth.tar",
    "checkpoints": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/checkpoints",
    "keep_checkpoint_max": 20,
    "leads": [
        "I",
        "II",
        "III",
        "V2"
    ],
    "fs": 500,
    "data_format": "channel_first",
    "special_classes": [
        "Brady",
        "LAD",
        "RAD",
        "PR",
        "LQRSV"
    ],
    "normalize_data": True,
    "train_ratio": 0.8,
    "min_class_weight": 0.5,
    "tranches_for_training": "",
    "tranche_class_weights": {
        "A": {
            "AF": 0.7604422604422605,
            "IAVB": 1.2860110803324099,
            "CLBBB": 3.9343220338983054,
            "NSR": 1.011437908496732,
            "PAC": 1.

ECG - INFO - training configurations are as follows:
{
    "db_dir": "/home/wenh06/Jupyter/data/CinC2021/",
    "log_dir": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/log",
    "model_dir": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/saved_models",
    "final_model_name": "4_lead_model_updated.pth.tar",
    "checkpoints": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/checkpoints",
    "keep_checkpoint_max": 20,
    "leads": [
        "I",
        "II",
        "III",
        "V2"
    ],
    "fs": 500,
    "data_format": "channel_first",
    "special_classes": [
        "Brady",
        "LAD",
        "RAD",
        "PR",
        "LQRSV"
    ],
    "normalize_data": True,
    "train_ratio": 0.8,
    "min_class_weight": 0.5,
    "tranches_for_training": "",
    "tranche_class_weights": {
        "A": {
            "AF": 0.7604422604422605,
            "IAVB": 1.2860110803324099,
            "CLBBB": 3.9343220338983054,
            "NSR": 1.011437908496732,
            "PAC": 1.

ECG - INFO - training configurations are as follows:
{
    "db_dir": "/home/wenh06/Jupyter/data/CinC2021/",
    "log_dir": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/log",
    "model_dir": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/saved_models",
    "final_model_name": "4_lead_model_updated.pth.tar",
    "checkpoints": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/checkpoints",
    "keep_checkpoint_max": 20,
    "leads": [
        "I",
        "II",
        "III",
        "V2"
    ],
    "fs": 500,
    "data_format": "channel_first",
    "special_classes": [
        "Brady",
        "LAD",
        "RAD",
        "PR",
        "LQRSV"
    ],
    "normalize_data": True,
    "train_ratio": 0.8,
    "min_class_weight": 0.5,
    "tranches_for_training": "",
    "tranche_class_weights": {
        "A": {
            "AF": 0.7604422604422605,
            "IAVB": 1.2860110803324099,
            "CLBBB": 3.9343220338983054,
            "NSR": 1.011437908496732,
            "PAC": 1.

INFO:ECG:training configurations are as follows:
{
    "db_dir": "/home/wenh06/Jupyter/data/CinC2021/",
    "log_dir": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/log",
    "model_dir": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/saved_models",
    "final_model_name": "4_lead_model_updated.pth.tar",
    "checkpoints": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/checkpoints",
    "keep_checkpoint_max": 20,
    "leads": [
        "I",
        "II",
        "III",
        "V2"
    ],
    "fs": 500,
    "data_format": "channel_first",
    "special_classes": [
        "Brady",
        "LAD",
        "RAD",
        "PR",
        "LQRSV"
    ],
    "normalize_data": True,
    "train_ratio": 0.8,
    "min_class_weight": 0.5,
    "tranches_for_training": "",
    "tranche_class_weights": {
        "A": {
            "AF": 0.7604422604422605,
            "IAVB": 1.2860110803324099,
            "CLBBB": 3.9343220338983054,
            "NSR": 1.011437908496732,
            "PAC": 1.5073

log file path is set /home/wenh06/Jupyter/wenhao/workspace/cinc2021/working_dir/CinC2021-CinC2021.log
levels of c_handler and f_handler are set DEBUG

start performing train test split...

train test split finished in 0.02 minutes
log file path is set /home/wenh06/Jupyter/wenhao/workspace/cinc2021/working_dir/CinC2021-CinC2021.log
levels of c_handler and f_handler are set DEBUG

start performing train test split...

train test split finished in 0.02 minutes
log file path is set /home/wenh06/Jupyter/wenhao/workspace/cinc2021/working_dir/CinC2021-CinC2021.log
levels of c_handler and f_handler are set DEBUG

start performing train test split...

train test split finished in 0.02 minutes
ECG - INFO - 
Starting training:
------------------
Epochs:          40
Batch size:      256
Learning rate:   0.001
Training size:   61944
Validation size: 15505
Device:          cuda
Optimizer:       adamw_amsgrad
Dataset classes: ['AF', 'AFL', 'BBB', 'CLBBB', 'CRBBB', 'IAVB', 'IRBBB', 'LAnFB', 'LPR', 'LQ

...

INFO:ECG:
Train epoch_34:
--------------------
train/epoch_loss:        100.1865303516388
train/auroc:             0.9906018097050144
train/auprc:             0.9315725946740178
train/accuracy:          0.7368429549270309
train/f_measure:         0.8520657735195514
train/f_beta_measure:    0.8202009262039912
train/g_beta_measure:    0.67045456876158
train/challenge_metric:  0.7530184272170809

test/auroc:              0.912175500323051
test/auprc:              0.5726484051166819
test/accuracy:           0.6165752982908739
test/f_measure:          0.5370314254345195
test/f_beta_measure:     0.5073263675333922
test/g_beta_measure:     0.33578777840402574
test/challenge_metric:   0.5986631653226365
---------------------------------



ECG - INFO - early stopping is triggered at epoch 34
ECG - INFO - early stopping is triggered at epoch 34
ECG - INFO - early stopping is triggered at epoch 34


INFO:ECG:early stopping is triggered at epoch 34
Epoch 34/40: 100%|█████████████████████████| 61944/61944 [11:05<00:00, 93.02it/s, loss (batch)=0.44]

ECG - INFO - Best model saved to /home/wenh06/Jupyter/wenhao/workspace/cinc2021/saved_models/4_lead_model_updated.pth.tar!
ECG - INFO - Best model saved to /home/wenh06/Jupyter/wenhao/workspace/cinc2021/saved_models/4_lead_model_updated.pth.tar!
ECG - INFO - Best model saved to /home/wenh06/Jupyter/wenhao/workspace/cinc2021/saved_models/4_lead_model_updated.pth.tar!



INFO:ECG:Best model saved to /home/wenh06/Jupyter/wenhao/workspace/cinc2021/saved_models/4_lead_model_updated.pth.tar!


In [ ]:
logging.shutdown()

In [31]:
with torch.no_grad():
    torch.cuda.empty_cache()

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

### train 3-lead model

In [32]:
config.leads = three_leads
config.n_leads = 3
config.final_model_name = ModelFilename[3]

config.batch_size = 256

model_config = deepcopy(ModelCfg.three_leads)
model_config.cnn.name = config.cnn_name
model_config.rnn.name = config.rnn_name
model_config.attn.name = config.attn_name

In [33]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

import logging
logger = logging.getLogger()
logger.handlers = []

logger = init_logger(log_dir=config.log_dir, verbose=2)
logger.info(f"\n{'*'*20}   Start Training   {'*'*20}\n")
logger.info(f"Using device {device}")
logger.info(f"Using torch of version {torch.__version__}")
logger.info(f"with configuration\n{dict_to_str(config)}")

tranches = config.tranches_for_training
if tranches:
    classes = config.tranche_classes[tranches]
else:
    classes = config.classes

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

log file path: /home/wenh06/Jupyter/wenhao/workspace/cinc2021/log/log_07-14_10-57.txt
levels of c_handler and f_handler are set DEBUG
ECG - INFO - 
********************   Start Training   ********************

ECG - INFO - 
********************   Start Training   ********************

ECG - INFO - 
********************   Start Training   ********************

ECG - INFO - 
********************   Start Training   ********************

ECG - INFO - Using device cuda
ECG - INFO - Using device cuda
ECG - INFO - Using device cuda
ECG - INFO - Using device cuda


<IPython.core.display.Javascript object>

ECG - INFO - Using torch of version 1.8.1+cu111
ECG - INFO - Using torch of version 1.8.1+cu111
ECG - INFO - Using torch of version 1.8.1+cu111
ECG - INFO - Using torch of version 1.8.1+cu111
ECG - INFO - with configuration
{
    "db_dir": "/home/wenh06/Jupyter/data/CinC2021/",
    "log_dir": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/log",
    "model_dir": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/saved_models",
    "final_model_name": "3_lead_model_updated.pth.tar",
    "checkpoints": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/checkpoints",
    "keep_checkpoint_max": 20,
    "leads": [
        "I",
        "II",
        "V2"
    ],
    "fs": 500,
    "data_format": "channel_first",
    "special_classes": [
        "Brady",
        "LAD",
        "RAD",
        "PR",
        "LQRSV"
    ],
    "normalize_data": True,
    "train_ratio": 0.8,
    "min_class_weight": 0.5,
    "tranches_for_training": "",
    "tranche_class_weights": {
        "A": {
            "AF": 0.76

ECG - INFO - with configuration
{
    "db_dir": "/home/wenh06/Jupyter/data/CinC2021/",
    "log_dir": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/log",
    "model_dir": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/saved_models",
    "final_model_name": "3_lead_model_updated.pth.tar",
    "checkpoints": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/checkpoints",
    "keep_checkpoint_max": 20,
    "leads": [
        "I",
        "II",
        "V2"
    ],
    "fs": 500,
    "data_format": "channel_first",
    "special_classes": [
        "Brady",
        "LAD",
        "RAD",
        "PR",
        "LQRSV"
    ],
    "normalize_data": True,
    "train_ratio": 0.8,
    "min_class_weight": 0.5,
    "tranches_for_training": "",
    "tranche_class_weights": {
        "A": {
            "AF": 0.7604422604422605,
            "IAVB": 1.2860110803324099,
            "CLBBB": 3.9343220338983054,
            "NSR": 1.011437908496732,
            "PAC": 1.5073051948051948,
            "CRBBB

ECG - INFO - with configuration
{
    "db_dir": "/home/wenh06/Jupyter/data/CinC2021/",
    "log_dir": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/log",
    "model_dir": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/saved_models",
    "final_model_name": "3_lead_model_updated.pth.tar",
    "checkpoints": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/checkpoints",
    "keep_checkpoint_max": 20,
    "leads": [
        "I",
        "II",
        "V2"
    ],
    "fs": 500,
    "data_format": "channel_first",
    "special_classes": [
        "Brady",
        "LAD",
        "RAD",
        "PR",
        "LQRSV"
    ],
    "normalize_data": True,
    "train_ratio": 0.8,
    "min_class_weight": 0.5,
    "tranches_for_training": "",
    "tranche_class_weights": {
        "A": {
            "AF": 0.7604422604422605,
            "IAVB": 1.2860110803324099,
            "CLBBB": 3.9343220338983054,
            "NSR": 1.011437908496732,
            "PAC": 1.5073051948051948,
            "CRBBB

In [34]:
model = ECG_CRNN_CINC2021(
    classes=classes,
    n_leads=config.n_leads,
    config=model_config,
)
model.__DEBUG__ = False

if torch.cuda.device_count() > 1:
    model = DP(model)
    # model = DDP(model)
model.to(device=device)

classes (totally 21) for prediction:['AF', 'AFL', 'BBB', 'CLBBB', 'CRBBB', 'IAVB', 'IRBBB', 'LAnFB', 'LPR', 'LQT', 'NSIVCB', 'NSR', 'PAC', 'PRWP', 'PVC', 'QAb', 'SA', 'SB', 'STach', 'TAb', 'TInv']
configuration of ECG_CRNN_CINC2021 is as follows
{
    "cnn": {
        "name": "multi_scopic_leadwise",
        "vgg16": {
            "num_convs": [
                2, 2, 3, 3, 3
            ],
            "num_filters": [
                48, 96, 192, 384, 384
            ],
            "groups": 1,
            "kernel_initializer": "he_normal",
            "kw_initializer": {},
            "activation": "relu",
            "kw_activation": {},
            "block": {
                "filter_length": 3,
                "subsample_length": 1,
                "dilation": 1,
                "batch_norm": True,
                "pool_size": 3,
                "pool_stride": 2,
                "kernel_initializer": "he_normal",
                "kw_initializer": {},
                "activation": "r

<IPython.core.display.Javascript object>

DataParallel(
  (module): ECG_CRNN_CINC2021(
    (cnn): MultiScopicCNN(
      (branches): ModuleDict(
        (branch_0): MultiScopicBranch(
          (block_0): MultiScopicBasicBlock(
            (ca_0): Conv_Bn_Activation(
              (conv1d): Conv1d(3, 96, kernel_size=(11,), stride=(1,), padding=(5,), groups=3)
              (batch_norm): GroupNorm(3, 96, eps=1e-05, affine=True)
              (activation_relu): ReLU(inplace=True)
            )
            (bn): BatchNorm1d(96, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
            (down): DownSample(
              (down_sample): MaxPool1d(kernel_size=2, stride=2, padding=0, dilation=1, ceil_mode=False)
            )
          )
          (block_1): MultiScopicBasicBlock(
            (ca_0): Conv_Bn_Activation(
              (conv1d): Conv1d(96, 192, kernel_size=(7,), stride=(1,), padding=(3,), groups=3)
              (batch_norm): GroupNorm(3, 192, eps=1e-05, affine=True)
              (activation_relu): ReLU

In [35]:
final_model = train(
    model=model,
    model_config=model_config,
    config=config,
    device=device,
    logger=logger,
    debug=True,
)

ECG - INFO - training configurations are as follows:
{
    "db_dir": "/home/wenh06/Jupyter/data/CinC2021/",
    "log_dir": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/log",
    "model_dir": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/saved_models",
    "final_model_name": "3_lead_model_updated.pth.tar",
    "checkpoints": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/checkpoints",
    "keep_checkpoint_max": 20,
    "leads": [
        "I",
        "II",
        "V2"
    ],
    "fs": 500,
    "data_format": "channel_first",
    "special_classes": [
        "Brady",
        "LAD",
        "RAD",
        "PR",
        "LQRSV"
    ],
    "normalize_data": True,
    "train_ratio": 0.8,
    "min_class_weight": 0.5,
    "tranches_for_training": "",
    "tranche_class_weights": {
        "A": {
            "AF": 0.7604422604422605,
            "IAVB": 1.2860110803324099,
            "CLBBB": 3.9343220338983054,
            "NSR": 1.011437908496732,
            "PAC": 1.507305194805194

ECG - INFO - training configurations are as follows:
{
    "db_dir": "/home/wenh06/Jupyter/data/CinC2021/",
    "log_dir": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/log",
    "model_dir": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/saved_models",
    "final_model_name": "3_lead_model_updated.pth.tar",
    "checkpoints": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/checkpoints",
    "keep_checkpoint_max": 20,
    "leads": [
        "I",
        "II",
        "V2"
    ],
    "fs": 500,
    "data_format": "channel_first",
    "special_classes": [
        "Brady",
        "LAD",
        "RAD",
        "PR",
        "LQRSV"
    ],
    "normalize_data": True,
    "train_ratio": 0.8,
    "min_class_weight": 0.5,
    "tranches_for_training": "",
    "tranche_class_weights": {
        "A": {
            "AF": 0.7604422604422605,
            "IAVB": 1.2860110803324099,
            "CLBBB": 3.9343220338983054,
            "NSR": 1.011437908496732,
            "PAC": 1.507305194805194

ECG - INFO - training configurations are as follows:
{
    "db_dir": "/home/wenh06/Jupyter/data/CinC2021/",
    "log_dir": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/log",
    "model_dir": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/saved_models",
    "final_model_name": "3_lead_model_updated.pth.tar",
    "checkpoints": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/checkpoints",
    "keep_checkpoint_max": 20,
    "leads": [
        "I",
        "II",
        "V2"
    ],
    "fs": 500,
    "data_format": "channel_first",
    "special_classes": [
        "Brady",
        "LAD",
        "RAD",
        "PR",
        "LQRSV"
    ],
    "normalize_data": True,
    "train_ratio": 0.8,
    "min_class_weight": 0.5,
    "tranches_for_training": "",
    "tranche_class_weights": {
        "A": {
            "AF": 0.7604422604422605,
            "IAVB": 1.2860110803324099,
            "CLBBB": 3.9343220338983054,
            "NSR": 1.011437908496732,
            "PAC": 1.507305194805194

ECG - INFO - training configurations are as follows:
{
    "db_dir": "/home/wenh06/Jupyter/data/CinC2021/",
    "log_dir": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/log",
    "model_dir": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/saved_models",
    "final_model_name": "3_lead_model_updated.pth.tar",
    "checkpoints": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/checkpoints",
    "keep_checkpoint_max": 20,
    "leads": [
        "I",
        "II",
        "V2"
    ],
    "fs": 500,
    "data_format": "channel_first",
    "special_classes": [
        "Brady",
        "LAD",
        "RAD",
        "PR",
        "LQRSV"
    ],
    "normalize_data": True,
    "train_ratio": 0.8,
    "min_class_weight": 0.5,
    "tranches_for_training": "",
    "tranche_class_weights": {
        "A": {
            "AF": 0.7604422604422605,
            "IAVB": 1.2860110803324099,
            "CLBBB": 3.9343220338983054,
            "NSR": 1.011437908496732,
            "PAC": 1.507305194805194

log file path is set /home/wenh06/Jupyter/wenhao/workspace/cinc2021/working_dir/CinC2021-CinC2021.log
levels of c_handler and f_handler are set DEBUG

start performing train test split...

train test split finished in 0.02 minutes
log file path is set /home/wenh06/Jupyter/wenhao/workspace/cinc2021/working_dir/CinC2021-CinC2021.log
levels of c_handler and f_handler are set DEBUG

start performing train test split...

train test split finished in 0.02 minutes
log file path is set /home/wenh06/Jupyter/wenhao/workspace/cinc2021/working_dir/CinC2021-CinC2021.log
levels of c_handler and f_handler are set DEBUG

start performing train test split...

train test split finished in 0.02 minutes
ECG - INFO - 
Starting training:
------------------
Epochs:          40
Batch size:      256
Learning rate:   0.001
Training size:   61944
Validation size: 15505
Device:          cuda
Optimizer:       adamw_amsgrad
Dataset classes: ['AF', 'AFL', 'BBB', 'CLBBB', 'CRBBB', 'IAVB', 'IRBBB', 'LAnFB', 'LPR', 'LQ

...

ECG - DEBUG - all_scalar_preds.shape = (61944, 21), all_labels.shape = (61944, 21)
ECG - DEBUG - all_scalar_preds.shape = (61944, 21), all_labels.shape = (61944, 21)
ECG - DEBUG - all_scalar_preds.shape = (61944, 21), all_labels.shape = (61944, 21)
ECG - DEBUG - all_scalar_preds.shape = (61944, 21), all_labels.shape = (61944, 21)
ECG - DEBUG - 
----------------------------------------------
scalar prediction:    [0.006, 0.004, 0.013, 0.004, 0.001, 0.01, 0.011, 0.004, 0.005, 0.002, 0.024, 0.014, 0.002, 0.005, 0.006, 0.021, 0.061, 0.86, 0.003, 0.046, 0.003]
binary prediction:    [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0]
labels:               [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0]
predicted classes:    ['SB']
label classes:        ['SB']
----------------------------------------------

ECG - DEBUG - 
----------------------------------------------
scalar prediction:    [0.006, 0.004, 0.013, 0.004, 0.001, 0.01, 0.011, 0.004, 0.005, 0.002, 0.024,

ECG - DEBUG - 
----------------------------------------------
scalar prediction:    [0.007, 0.004, 0.006, 0.004, 0.002, 0.007, 0.004, 0.008, 0.004, 0.006, 0.002, 0.966, 0.002, 0.006, 0.004, 0.001, 0.003, 0.003, 0.006, 0.557, 0.019]
binary prediction:    [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 1, 0]
labels:               [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 1, 0]
predicted classes:    ['NSR', 'TAb']
label classes:        ['NSR', 'TAb']
----------------------------------------------

ECG - DEBUG - 
----------------------------------------------
scalar prediction:    [0.007, 0.004, 0.006, 0.004, 0.002, 0.007, 0.004, 0.008, 0.004, 0.006, 0.002, 0.966, 0.002, 0.006, 0.004, 0.001, 0.003, 0.003, 0.006, 0.557, 0.019]
binary prediction:    [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 1, 0]
labels:               [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 1, 0]
predicted classes:    ['NSR', 'TAb']
label classes:        ['NSR', 'TA

ECG - DEBUG - 
----------------------------------------------
scalar prediction:    [0.02, 0.003, 0.005, 0.005, 0.005, 0.003, 0.156, 0.003, 0.005, 0.002, 0.015, 0.928, 0.002, 0.003, 0.003, 0.008, 0.316, 0.004, 0.001, 0.013, 0.002]
binary prediction:    [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0]
labels:               [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0]
predicted classes:    ['NSR']
label classes:        ['NSR']
----------------------------------------------

ECG - DEBUG - 
----------------------------------------------
scalar prediction:    [0.02, 0.003, 0.005, 0.005, 0.005, 0.003, 0.156, 0.003, 0.005, 0.002, 0.015, 0.928, 0.002, 0.003, 0.003, 0.008, 0.316, 0.004, 0.001, 0.013, 0.002]
binary prediction:    [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0]
labels:               [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0]
predicted classes:    ['NSR']
label classes:        ['NSR']
--------------------------

Epoch 28/40: 100%|███████████████████████| 61944/61944 [08:37<00:00, 119.81it/s, loss (batch)=0.416]

ECG - INFO - Best model saved to /home/wenh06/Jupyter/wenhao/workspace/cinc2021/saved_models/3_lead_model_updated.pth.tar!
ECG - INFO - Best model saved to /home/wenh06/Jupyter/wenhao/workspace/cinc2021/saved_models/3_lead_model_updated.pth.tar!
ECG - INFO - Best model saved to /home/wenh06/Jupyter/wenhao/workspace/cinc2021/saved_models/3_lead_model_updated.pth.tar!
ECG - INFO - Best model saved to /home/wenh06/Jupyter/wenhao/workspace/cinc2021/saved_models/3_lead_model_updated.pth.tar!


In [ ]:
logging.shutdown()

In [36]:
with torch.no_grad():
    torch.cuda.empty_cache()

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

### train 2-lead model

In [37]:
config.leads = two_leads
config.n_leads = 2
config.final_model_name = ModelFilename[2]

config.batch_size = 256

model_config = deepcopy(ModelCfg.two_leads)
model_config.cnn.name = config.cnn_name
model_config.rnn.name = config.rnn_name
model_config.attn.name = config.attn_name

In [38]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

del logger

logger = init_logger(log_dir=config.log_dir, verbose=2)
logger.info(f"\n{'*'*20}   Start Training   {'*'*20}\n")
logger.info(f"Using device {device}")
logger.info(f"Using torch of version {torch.__version__}")
logger.info(f"with configuration\n{dict_to_str(config)}")

tranches = config.tranches_for_training
if tranches:
    classes = config.tranche_classes[tranches]
else:
    classes = config.classes

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

log file path: /home/wenh06/Jupyter/wenhao/workspace/cinc2021/log/log_07-14_14-41.txt
levels of c_handler and f_handler are set DEBUG
ECG - INFO - 
********************   Start Training   ********************

ECG - INFO - 
********************   Start Training   ********************

ECG - INFO - 
********************   Start Training   ********************

ECG - INFO - 
********************   Start Training   ********************

ECG - INFO - 
********************   Start Training   ********************

ECG - INFO - Using device cuda
ECG - INFO - Using device cuda
ECG - INFO - Using device cuda
ECG - INFO - Using device cuda
ECG - INFO - Using device cuda


<IPython.core.display.Javascript object>

ECG - INFO - Using torch of version 1.8.1+cu111
ECG - INFO - Using torch of version 1.8.1+cu111
ECG - INFO - Using torch of version 1.8.1+cu111
ECG - INFO - Using torch of version 1.8.1+cu111
ECG - INFO - Using torch of version 1.8.1+cu111
ECG - INFO - with configuration
{
    "db_dir": "/home/wenh06/Jupyter/data/CinC2021/",
    "log_dir": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/log",
    "model_dir": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/saved_models",
    "final_model_name": "2_lead_model_updated.pth.tar",
    "checkpoints": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/checkpoints",
    "keep_checkpoint_max": 20,
    "leads": [
        "I",
        "II"
    ],
    "fs": 500,
    "data_format": "channel_first",
    "special_classes": [
        "Brady",
        "LAD",
        "RAD",
        "PR",
        "LQRSV"
    ],
    "normalize_data": True,
    "train_ratio": 0.8,
    "min_class_weight": 0.5,
    "tranches_for_training": "",
    "tranche_class_weights": {
   

ECG - INFO - with configuration
{
    "db_dir": "/home/wenh06/Jupyter/data/CinC2021/",
    "log_dir": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/log",
    "model_dir": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/saved_models",
    "final_model_name": "2_lead_model_updated.pth.tar",
    "checkpoints": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/checkpoints",
    "keep_checkpoint_max": 20,
    "leads": [
        "I",
        "II"
    ],
    "fs": 500,
    "data_format": "channel_first",
    "special_classes": [
        "Brady",
        "LAD",
        "RAD",
        "PR",
        "LQRSV"
    ],
    "normalize_data": True,
    "train_ratio": 0.8,
    "min_class_weight": 0.5,
    "tranches_for_training": "",
    "tranche_class_weights": {
        "A": {
            "AF": 0.7604422604422605,
            "IAVB": 1.2860110803324099,
            "CLBBB": 3.9343220338983054,
            "NSR": 1.011437908496732,
            "PAC": 1.5073051948051948,
            "CRBBB": 0.5
       

ECG - INFO - with configuration
{
    "db_dir": "/home/wenh06/Jupyter/data/CinC2021/",
    "log_dir": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/log",
    "model_dir": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/saved_models",
    "final_model_name": "2_lead_model_updated.pth.tar",
    "checkpoints": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/checkpoints",
    "keep_checkpoint_max": 20,
    "leads": [
        "I",
        "II"
    ],
    "fs": 500,
    "data_format": "channel_first",
    "special_classes": [
        "Brady",
        "LAD",
        "RAD",
        "PR",
        "LQRSV"
    ],
    "normalize_data": True,
    "train_ratio": 0.8,
    "min_class_weight": 0.5,
    "tranches_for_training": "",
    "tranche_class_weights": {
        "A": {
            "AF": 0.7604422604422605,
            "IAVB": 1.2860110803324099,
            "CLBBB": 3.9343220338983054,
            "NSR": 1.011437908496732,
            "PAC": 1.5073051948051948,
            "CRBBB": 0.5
       

In [39]:
model = ECG_CRNN_CINC2021(
    classes=classes,
    n_leads=config.n_leads,
    config=model_config,
)
model.__DEBUG__ = False

if torch.cuda.device_count() > 1:
    model = DP(model)
    # model = DDP(model)
model.to(device=device)

classes (totally 21) for prediction:['AF', 'AFL', 'BBB', 'CLBBB', 'CRBBB', 'IAVB', 'IRBBB', 'LAnFB', 'LPR', 'LQT', 'NSIVCB', 'NSR', 'PAC', 'PRWP', 'PVC', 'QAb', 'SA', 'SB', 'STach', 'TAb', 'TInv']
configuration of ECG_CRNN_CINC2021 is as follows
{
    "cnn": {
        "name": "multi_scopic_leadwise",
        "vgg16": {
            "num_convs": [
                2, 2, 3, 3, 3
            ],
            "num_filters": [
                48, 96, 192, 384, 384
            ],
            "groups": 1,
            "kernel_initializer": "he_normal",
            "kw_initializer": {},
            "activation": "relu",
            "kw_activation": {},
            "block": {
                "filter_length": 3,
                "subsample_length": 1,
                "dilation": 1,
                "batch_norm": True,
                "pool_size": 3,
                "pool_stride": 2,
                "kernel_initializer": "he_normal",
                "kw_initializer": {},
                "activation": "r

<IPython.core.display.Javascript object>

DataParallel(
  (module): ECG_CRNN_CINC2021(
    (cnn): MultiScopicCNN(
      (branches): ModuleDict(
        (branch_0): MultiScopicBranch(
          (block_0): MultiScopicBasicBlock(
            (ca_0): Conv_Bn_Activation(
              (conv1d): Conv1d(2, 64, kernel_size=(11,), stride=(1,), padding=(5,), groups=2)
              (batch_norm): GroupNorm(2, 64, eps=1e-05, affine=True)
              (activation_relu): ReLU(inplace=True)
            )
            (bn): BatchNorm1d(64, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
            (down): DownSample(
              (down_sample): MaxPool1d(kernel_size=2, stride=2, padding=0, dilation=1, ceil_mode=False)
            )
          )
          (block_1): MultiScopicBasicBlock(
            (ca_0): Conv_Bn_Activation(
              (conv1d): Conv1d(64, 128, kernel_size=(7,), stride=(1,), padding=(3,), groups=2)
              (batch_norm): GroupNorm(2, 128, eps=1e-05, affine=True)
              (activation_relu): ReLU

In [40]:
final_model = train(
    model=model,
    model_config=model_config,
    config=config,
    device=device,
    logger=logger,
    debug=True,
)

ECG - INFO - training configurations are as follows:
{
    "db_dir": "/home/wenh06/Jupyter/data/CinC2021/",
    "log_dir": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/log",
    "model_dir": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/saved_models",
    "final_model_name": "2_lead_model_updated.pth.tar",
    "checkpoints": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/checkpoints",
    "keep_checkpoint_max": 20,
    "leads": [
        "I",
        "II"
    ],
    "fs": 500,
    "data_format": "channel_first",
    "special_classes": [
        "Brady",
        "LAD",
        "RAD",
        "PR",
        "LQRSV"
    ],
    "normalize_data": True,
    "train_ratio": 0.8,
    "min_class_weight": 0.5,
    "tranches_for_training": "",
    "tranche_class_weights": {
        "A": {
            "AF": 0.7604422604422605,
            "IAVB": 1.2860110803324099,
            "CLBBB": 3.9343220338983054,
            "NSR": 1.011437908496732,
            "PAC": 1.5073051948051948,
           

ECG - INFO - training configurations are as follows:
{
    "db_dir": "/home/wenh06/Jupyter/data/CinC2021/",
    "log_dir": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/log",
    "model_dir": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/saved_models",
    "final_model_name": "2_lead_model_updated.pth.tar",
    "checkpoints": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/checkpoints",
    "keep_checkpoint_max": 20,
    "leads": [
        "I",
        "II"
    ],
    "fs": 500,
    "data_format": "channel_first",
    "special_classes": [
        "Brady",
        "LAD",
        "RAD",
        "PR",
        "LQRSV"
    ],
    "normalize_data": True,
    "train_ratio": 0.8,
    "min_class_weight": 0.5,
    "tranches_for_training": "",
    "tranche_class_weights": {
        "A": {
            "AF": 0.7604422604422605,
            "IAVB": 1.2860110803324099,
            "CLBBB": 3.9343220338983054,
            "NSR": 1.011437908496732,
            "PAC": 1.5073051948051948,
           

ECG - INFO - training configurations are as follows:
{
    "db_dir": "/home/wenh06/Jupyter/data/CinC2021/",
    "log_dir": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/log",
    "model_dir": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/saved_models",
    "final_model_name": "2_lead_model_updated.pth.tar",
    "checkpoints": "/home/wenh06/Jupyter/wenhao/workspace/cinc2021/checkpoints",
    "keep_checkpoint_max": 20,
    "leads": [
        "I",
        "II"
    ],
    "fs": 500,
    "data_format": "channel_first",
    "special_classes": [
        "Brady",
        "LAD",
        "RAD",
        "PR",
        "LQRSV"
    ],
    "normalize_data": True,
    "train_ratio": 0.8,
    "min_class_weight": 0.5,
    "tranches_for_training": "",
    "tranche_class_weights": {
        "A": {
            "AF": 0.7604422604422605,
            "IAVB": 1.2860110803324099,
            "CLBBB": 3.9343220338983054,
            "NSR": 1.011437908496732,
            "PAC": 1.5073051948051948,
           


start performing train test split...

train test split finished in 0.02 minutes
log file path is set /home/wenh06/Jupyter/wenhao/workspace/cinc2021/working_dir/CinC2021-CinC2021.log
levels of c_handler and f_handler are set DEBUG

start performing train test split...

train test split finished in 0.02 minutes
log file path is set /home/wenh06/Jupyter/wenhao/workspace/cinc2021/working_dir/CinC2021-CinC2021.log
levels of c_handler and f_handler are set DEBUG

start performing train test split...

train test split finished in 0.02 minutes
ECG - INFO - 
Starting training:
------------------
Epochs:          40
Batch size:      256
Learning rate:   0.001
Training size:   61944
Validation size: 15505
Device:          cuda
Optimizer:       adamw_amsgrad
Dataset classes: ['AF', 'AFL', 'BBB', 'CLBBB', 'CRBBB', 'IAVB', 'IRBBB', 'LAnFB', 'LPR', 'LQT', 'NSIVCB', 'NSR', 'PAC', 'PRWP', 'PVC', 'QAb', 'SA', 'SB', 'STach', 'TAb', 'TInv']
Class weights:   tensor([[ 2.7578,  1.7252, 28.8333,  9.6690,  2

Epoch 1/40:   8%|██                        | 4864/61944 [00:17<02:09, 439.87it/s, loss (batch)=1.01]

...

ECG - DEBUG - 
----------------------------------------------
scalar prediction:    [0.005, 0.002, 0.01, 0.005, 0.047, 0.003, 0.005, 0.018, 0.005, 0.001, 0.003, 0.936, 0.002, 0.006, 0.001, 0.005, 0.003, 0.003, 0.019, 0.271, 0.037]
binary prediction:    [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0]
labels:               [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 1, 1]
predicted classes:    ['NSR']
label classes:        ['NSR', 'TAb', 'TInv']
----------------------------------------------

ECG - DEBUG - 
----------------------------------------------
scalar prediction:    [0.005, 0.002, 0.01, 0.005, 0.047, 0.003, 0.005, 0.018, 0.005, 0.001, 0.003, 0.936, 0.002, 0.006, 0.001, 0.005, 0.003, 0.003, 0.019, 0.271, 0.037]
binary prediction:    [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0]
labels:               [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 1, 1]
predicted classes:    ['NSR']
label classes:        ['NSR', 'TAb', 'TIn

ECG - DEBUG - 
----------------------------------------------
scalar prediction:    [0.003, 0.004, 0.006, 0.002, 0.028, 0.001, 0.005, 0.001, 0.005, 0.006, 0.002, 0.144, 0.003, 0.001, 0.006, 0.001, 0.043, 0.556, 0.002, 0.124, 0.022]
binary prediction:    [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0]
labels:               [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0]
predicted classes:    ['SB']
label classes:        ['SB']
----------------------------------------------

ECG - DEBUG - 
----------------------------------------------
scalar prediction:    [0.003, 0.004, 0.006, 0.002, 0.028, 0.001, 0.005, 0.001, 0.005, 0.006, 0.002, 0.144, 0.003, 0.001, 0.006, 0.001, 0.043, 0.556, 0.002, 0.124, 0.022]
binary prediction:    [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0]
labels:               [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0]
predicted classes:    ['SB']
label classes:        ['SB']
----------------------------

ECG - DEBUG - 
----------------------------------------------
scalar prediction:    [0.034, 0.807, 0.0, 0.01, 0.006, 0.002, 0.004, 0.002, 0.004, 0.016, 0.0, 0.08, 0.0, 0.003, 0.003, 0.004, 0.0, 0.001, 0.0, 0.023, 0.004]
binary prediction:    [0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
labels:               [0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
predicted classes:    ['AFL']
label classes:        ['AFL']
----------------------------------------------

ECG - DEBUG - 
----------------------------------------------
scalar prediction:    [0.034, 0.807, 0.0, 0.01, 0.006, 0.002, 0.004, 0.002, 0.004, 0.016, 0.0, 0.08, 0.0, 0.003, 0.003, 0.004, 0.0, 0.001, 0.0, 0.023, 0.004]
binary prediction:    [0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
labels:               [0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]
predicted classes:    ['AFL']
label classes:        ['AFL']
----------------------------------------------



Epoch 30/40: 100%|███████████████████████| 61944/61944 [07:30<00:00, 137.45it/s, loss (batch)=0.463]

ECG - INFO - Best model saved to /home/wenh06/Jupyter/wenhao/workspace/cinc2021/saved_models/2_lead_model_updated.pth.tar!
ECG - INFO - Best model saved to /home/wenh06/Jupyter/wenhao/workspace/cinc2021/saved_models/2_lead_model_updated.pth.tar!
ECG - INFO - Best model saved to /home/wenh06/Jupyter/wenhao/workspace/cinc2021/saved_models/2_lead_model_updated.pth.tar!
ECG - INFO - Best model saved to /home/wenh06/Jupyter/wenhao/workspace/cinc2021/saved_models/2_lead_model_updated.pth.tar!
ECG - INFO - Best model saved to /home/wenh06/Jupyter/wenhao/workspace/cinc2021/saved_models/2_lead_model_updated.pth.tar!


In [41]:
logging.shutdown()

# clear GPU cache

In [ ]:
with torch.no_grad():
    torch.cuda.empty_cache()

# Debug

In [ ]:
from data_reader import CINC2021Reader as DR
from dataset import CINC2021 as DG

In [ ]:
?DG

In [ ]:
dg = DG(TrainCfg)

In [ ]:
dg._check_nan()

In [ ]:
hehe_data = dg.reader.load_data("JS35065")

In [ ]:
plt.plot(hehe_data[11])

In [ ]:
from utils.scoring_aux_data import *

%load_ext autoreload
%autoreload 2

In [ ]:
dx_mapping_scored

In [ ]:
dx_mapping_all.columns.values

In [ ]:
equiv_class_dict

In [ ]:
dx_mapping_scored

In [ ]:
equiv_class_dict

In [ ]:
from data_reader import CINC2021Reader as DR

%load_ext autoreload
%autoreload 2

In [ ]:
dr = DR("/home/wenh06/Jupyter/data/CinC2021/")

In [ ]:
dr._compute_cooccurrence()

In [ ]:
dr.load_ann(dr.all_records.G[10420], raw=True)

In [ ]:
dr.load_ann(dr.all_records.G[332], raw=True)

In [ ]:
dr.all_records.G[333]

In [ ]:
dr.all_records.G[3139]

In [ ]:
251238007, 6180003